# Function for Basic Linear Regression on Cluster Plot
## Example Parameter: Avg Leaf Nitrogen Concentration (LNC) vs Leaf Carbon Nitrogen Ratio (LCN)
#### Author: Sofia Ingersoll, Sujan Bhattaria, & Heather Childers

##### Loading environment settings

In [9]:
# moved the libraries that were here into utils.py because they're essential
# xarray is required to run the utils import line
import xarray as xr
import pandas as pd
import glob
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
#from sklearn_xarray import Stacker, Select

import matplotlib.pyplot as plt
from dask_jobqueue import PBSCluster
from dask.distributed import Client

Something funky is happening with utils, I can't call it anymore and idk why.

In [10]:
# import libraries & data pre-processing functions from utils.py
from utils import *

ModuleNotFoundError: No module named 'utils'

pulling this chunk from utils to work 

In [11]:
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----  server request to aid processing  ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

def get_cluster(account,cores=30):    
    """Spin up a dask cluster.

    Keyword arguments:
    account -- your account number, e.g. 'UCSB0021'
    cores -- the number of processors requested

    Returns:
    client -- can be useful to inspect client.cluster or run client.close()
    """

    cluster = PBSCluster(
    # The number of cores you want
    cores=1,
    # Amount of memory
    memory='10GB',
     # How many processes
    processes=1,
    # The type of queue to utilize (/glade/u/apps/dav/opt/usr/bin/execcasper)
    queue='casper', 
    # Use your local directory
    local_directory = '$TMPDIR',
    # Specify resources
    resource_spec='select=1:ncpus=1:mem=10GB',
    # Input your project ID here
    account = account,
    # Amount of wall time
    walltime = '02:00:00',
    )

    # Scale up
    cluster.scale(cores)
    
    # Setup your client
    client = Client(cluster)

    return client

### Leaf Carbon : Nitrogen Data

This will come in handy later when we want to plot trends overtime

In [40]:
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----     load data stored in casper     ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#-------Gridcell Landareas Data-----
# reading, storing, subsetting
landarea_file = '/glade/campaign/cgd/tss/projects/PPE/helpers/sparsegrid_landarea.nc'

landarea_ds = xr.open_dataset(landarea_file)

landarea = landarea_ds['landarea']
#-------Dummy Variable Data---------
# dummy data to have stored for preloaded visual on 
dummy_filepath = '/glade/campaign/cgd/tss/projects/PPE/PPEn11_OAAT/CTL2010/hist/PPEn11_CTL2010_OAAT0000.clm2.h0.2005-02-01-00000.nc'

# dummy data described by filepath stored as ds
ds = xr.open_dataset(dummy_filepath)

# dummy variable data subset as data array. using LNC for linearity
#da = ds['LNC']

#-------Leaf Carbon : Nitrogen Data---------
# x variable data for plotting
df = pd.read_csv('/glade/campaign/asp/djk2120/PPEn11/csvs/lhc220926.txt',index_col=0)
# convert to data set
params = xr.Dataset(df)

# the only dimension here is the 'member' aka file index id [LCH0001-500]
params

# subsetting for leafcn
leafcn = params['leafcn']

#leafcn
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----     correct time-parsing bug       ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
def fix_time(ds):
    
    '''fix CESM monthly time-parsing bug'''
    
    yr0 = str(ds['time.year'][0].values)
    
    ds['time'] = xr.cftime_range(yr0,periods=len(ds.time),freq='MS',calendar='noleap')
    
    return ds


#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----  weigh dummy landarea by gridcell  ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#------Weight Gridcells by Landarea---
def weight_landarea_gridcells(ds,landarea):

    # weigh landarea variable by mean of gridcell dimension
    ds['landarea'] = ds.weighted(landarea).mean(dim = 'gridcell')              # changed to da['landarea'] instead of weighted_avg_area. should it be da.landarea?

    return ds                                           # This now works when importing utils (changed from weighted_avg_area)


#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----     weigh dummy data time dim      ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#------Weighted Averages by Time---
def yearly_weighted_average(ds):
    # Get the array of number of days from the main dataset
    days_in_month = ds['time.daysinmonth']

    # Multiply each month's data by corresponding days in month
    weighted_sum = (days_in_month*ds).groupby("time.year").sum(dim = 'time')

    # Total days in the year
    total_days = days_in_month.groupby("time.year").sum(dim = 'time')

    # Calculate weighted average for the year
    ds['time'] = weighted_sum / total_days            # This now works when importing utils. (changed from return weighted_sum / total_days)

    return ds

##### Request additional processing power from server

In [12]:
# Request an additional 10 cores of power for processing from the server
client = get_cluster("UCSB0021", cores = 40)

/glade/u/home/singersoll/.conda/envs/meds-py/lib/python3.11/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 46761 instead
  warnings.warn(


In [13]:
# apply peer2peer network communication across multiple devices
client.cluster

PBSCluster(6a58c548, 'tcp://128.117.208.88:44283', workers=13, threads=13, memory=121.03 GiB)

## Loading a Cluster of 500 files
The data files are located in `/glade/campaign/cgd/tss/projects/PPE/PPEn11_LHC/transient/hist/`

The 2005-2010 monthly output files have the form:
`PPEn11_transient_LHC0001.clm2.h0.2005-02-01-00000.nc`

We're interested in files spanning from:
`LHC0001 to LHC0500`

In [24]:
# modify the function if you want to pass the parameter
def read_all_simulation(var):
    '''prepare cluster list and read to create ensemble(group of data)
    use preprocess to select only certain dimension and a variable'''
    # read all simulations as a list
    cluster_list = sorted(glob.glob('/glade/campaign/cgd/tss/projects/PPE/PPEn11_LHC/transient/hist/PPEn11_transient_LHC[0][0-5][0-9][0-9].clm2.h0.2005-02-01-00000.nc'))
    cluster_list = cluster_list[1:len(cluster_list)]

    # only select latitude, longitude, time, and  using this in preprocess steps
    def preprocess_cluster (ds, var):
        '''using this function in xr.open_mfdataset as preprocess
        ensures that when only these four things are selected 
        before the data is combined'''
        return ds[['lat', 'lon', 'time', var]]

    # creating cluster
    #read the list and load it for the notebook
    xr.open_mfdataset( cluster_list, 
                                   combine='nested',
                                   preprocess = lambda ds: preprocess_cluster(ds, var),
                                   parallel=False, 
                                   concat_dim="ens")

Maybe I'm not applying the function correctly, but the object cluster_list is not callable outside of the function

In [16]:
# apply nested function to generate cluster list 
LNC = read_all_simulation('LNC')

In [25]:
# creating cluster
#read the list and load it for the notebook
LNC = xr.open_mfdataset( cluster_list, 
                                   combine='nested',
                                   preprocess = lambda ds: preprocess_cluster(ds, LNC),
                                   parallel=False, 
                                   concat_dim="ens")

NameError: name 'cluster_list' is not defined

Debugging Code 

This part is working perfectly

In [28]:
# read all simulations as a list
cluster_list = sorted(glob.glob('/glade/campaign/cgd/tss/projects/PPE/PPEn11_LHC/transient/hist/PPEn11_transient_LHC[0][0-5][0-9][0-9].clm2.h0.2005-02-01-00000.nc'))
cluster_list = cluster_list[1:len(cluster_list)]
#cluster_list

In [31]:
# creating cluster
#read the list and load it for the notebook
LNC = xr.open_mfdataset(cluster_list, 
                                   combine='nested',
                                   parallel=True, 
                                   concat_dim="ens")

In [36]:
# confirming that the ensemble loaded correctly! yay! ens: 500 
LNC

<xarray.Dataset>
Dimensions:                            (levgrnd: 25, levsoi: 20, levlak: 10,
                                        levdcmp: 25, time: 60, ens: 500,
                                        hist_interval: 2, lon: 144, lat: 96,
                                        gridcell: 400, landunit: 1267,
                                        column: 2974, pft: 8574, cft: 2,
                                        ltype: 9, nvegwcs: 4)
Coordinates:
  * levgrnd                            (levgrnd) float32 0.01 0.04 ... 42.0
  * levsoi                             (levsoi) float32 0.01 0.04 ... 6.94 8.03
  * levlak                             (levlak) float32 0.05 0.6 ... 34.33 44.78
  * levdcmp                            (levdcmp) float32 0.01 0.04 ... 42.0
  * time                               (time) object 2005-02-01 00:00:00 ... ...
  * lon                                (lon) float32 0.0 2.5 5.0 ... 355.0 357.5
  * lat                                (lat) float32 -90.0 -88.11 ... 88.11 90.0
Dimensions without coordinates: ens, hist_interval, gridcell, landunit, column,
                                pft, cft, ltype, nvegwcs
Data variables: (12/497)
    mcdate                             (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mcsec                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mdcur                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mscur                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    nstep                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    time_bounds                        (ens, time, hist_interval) object dask.array<chunksize=(1, 60, 2), meta=np.ndarray>
    ...                                 ...
    XSMRPOOL                           (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    XSMRPOOL_RECOVER                   (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZBOT                               (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT                                (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT_CH4_UNSAT                      (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT_PERCH                          (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
Attributes: (12/40)
    title:                                     CLM History file information
    comment:                                   NOTE: None of the variables ar...
    Conventions:                               CF-1.0
    history:                                   created on 08/10/23 00:09:45
    source:                                    Community Terrestrial Systems ...
    hostname:                                  cheyenne
    ...                                        ...
    ctype_urban_pervious_road:                 75
    cft_c3_crop:                               1
    cft_c3_irrigated:                          2
    time_period_freq:                          month_1
    Time_constant_3Dvars_filename:             ./PPEn11_transient_LHC0001.clm...
    Time_constant_3Dvars:                      ZSOI:DZSOI:WATSAT:SUCSAT:BSW:H...

## Wrangling Cluster for Avg LNC with properly weighted dimensions (time & gridcell) 

In [41]:
# testing to see if our functions can be applied to an ensemble
# time bug fixer funct
LNC = fix_time(LNC)                   # I don't think I need to set it equal because the function says return da, but just incase 

In [42]:
# they can! the time bug was fixed :-) 
LNC

<xarray.Dataset>
Dimensions:                            (levgrnd: 25, levsoi: 20, levlak: 10,
                                        levdcmp: 25, time: 60, ens: 500,
                                        hist_interval: 2, lon: 144, lat: 96,
                                        gridcell: 400, landunit: 1267,
                                        column: 2974, pft: 8574, cft: 2,
                                        ltype: 9, nvegwcs: 4)
Coordinates:
  * levgrnd                            (levgrnd) float32 0.01 0.04 ... 42.0
  * levsoi                             (levsoi) float32 0.01 0.04 ... 6.94 8.03
  * levlak                             (levlak) float32 0.05 0.6 ... 34.33 44.78
  * levdcmp                            (levdcmp) float32 0.01 0.04 ... 42.0
  * time                               (time) object 2005-01-01 00:00:00 ... ...
  * lon                                (lon) float32 0.0 2.5 5.0 ... 355.0 357.5
  * lat                                (lat) float32 -90.0 -88.11 ... 88.11 90.0
Dimensions without coordinates: ens, hist_interval, gridcell, landunit, column,
                                pft, cft, ltype, nvegwcs
Data variables: (12/497)
    mcdate                             (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mcsec                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mdcur                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    mscur                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    nstep                              (ens, time) int32 dask.array<chunksize=(1, 60), meta=np.ndarray>
    time_bounds                        (ens, time, hist_interval) object dask.array<chunksize=(1, 60, 2), meta=np.ndarray>
    ...                                 ...
    XSMRPOOL                           (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    XSMRPOOL_RECOVER                   (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZBOT                               (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT                                (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT_CH4_UNSAT                      (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
    ZWT_PERCH                          (ens, time, gridcell) float32 dask.array<chunksize=(1, 60, 400), meta=np.ndarray>
Attributes: (12/40)
    title:                                     CLM History file information
    comment:                                   NOTE: None of the variables ar...
    Conventions:                               CF-1.0
    history:                                   created on 08/10/23 00:09:45
    source:                                    Community Terrestrial Systems ...
    hostname:                                  cheyenne
    ...                                        ...
    ctype_urban_pervious_road:                 75
    cft_c3_crop:                               1
    cft_c3_irrigated:                          2
    time_period_freq:                          month_1
    Time_constant_3Dvars_filename:             ./PPEn11_transient_LHC0001.clm...
    Time_constant_3Dvars:                      ZSOI:DZSOI:WATSAT:SUCSAT:BSW:H...

In [44]:
# testing weighting time
LNC = yearly_weighted_average(LNC)

TypeError: operand type(s) all returned NotImplemented from __array_ufunc__(<ufunc 'multiply'>, '__call__', array([[31],
       [28],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [28],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [28],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [28],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [28],
       [31],
       [30],
       [31],
       [30],
       [31],
       [31],
       [30],
       [31],
       [30],
       [31]]), dask.array<transpose, shape=(60, 500), dtype=|S16, chunksize=(60, 1), chunktype=numpy.ndarray>): 'ndarray', 'A

In [45]:
# weighting grid cells
LNC = weight_landarea_gridcells(LNC, landarea)

UFuncTypeError: ufunc 'add' did not contain a loop with signature matching types (dtype('S32'), dtype('S32')) -> None

### Visualize Cluster Plot with Linear Regression

In [ ]:
# Creating Linear Regression for LNC

# using utils pre-processed data array for LNC
# split into training & testing (90/10)
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----      Split Data 90/10        ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
da = da.dropna('gridcell')

X_train, X_test, y_train, y_test = train_test_split(leafcn_da, da, test_size = 0.1, random_state=0)


#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----      Linear Regression       ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
regressor = LinearRegression()
regressor.fit(X_train, y_train)

LinearRegression()

y_pred = regressor.predict(X_test)

#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# ----    Plot Linear Regression    ----
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
plt.scatter(X_train, y_train,color='g')
plt.plot(X_test, y_pred,color='k')

plt.show()

In [38]:
# plot mean tsa overtime of weighted gridcells
#plt.figure(figsize = (9,4))
#plt.scatter(leafcn,
 #           LNC,
  #          c = LNC_avg,
   #        cmap = 'RdPu',
    #       alpha = 0.5)
#plt.xlabel('Leaf Carbon Nitrogen Ratio')
#plt.ylabel('Leaf Nitrogen Concentration')
#plt.title('Default Simulation: OAAT0000')
#plt.colorbar(label = 'Concenctration (units to be added)')